# Optimize Initial Conditions
## Yabox

In [1]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from yabox import DE

# Initialize Ray

In [2]:
from environs import Env
env = Env()
env.str("CUDA_DEVICE_ORDER",'PCI_BUS_ID')
env.int("CUDA_VISIBLE_DEVICES",1)
env.int("NUMBA_ENABLE_CUDASIM",1)
env.bool("OMPI_MCA_opal_cuda_support",True)

import os
import ray
MB=1024*1024
GB=MB*1024
ray.shutdown()
ray.init(object_store_memory=1*GB,memory=220*GB,
         #lru_evict=True,
         driver_object_store_memory=500*MB,num_gpus=1,num_cpus=1,
         ignore_reinit_error=True) # , include_webui=False, ignore_reinit_error=True)

@ray.remote(num_gpus=1)
def use_gpu():
    print("ray.get_gpu_ids(): {}".format(ray.get_gpu_ids()[0]))
    print("CUDA_VISIBLE_DEVICES: {}".format(os.environ["CUDA_VISIBLE_DEVICES"]))

use_gpu.remote()

2020-09-13 11:15:35,328	INFO resource_spec.py:212 -- Starting Ray with 219.97 GiB memory available for workers and up to 1.0 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-09-13 11:15:35,702	INFO services.py:1170 -- View the Ray dashboard at localhost:8266


ObjectID(45b95b1c8bd3a9c4ffffffff010000c801000000)

# Load New and Process Data from website data.brasil.io

In [3]:
%reload_ext autoreload
%autoreload 2
import get_data
LoadData=True

if LoadData:
    get_data.get_data()

Baixando arquivos brasil.io...
(pid=19844) ray.get_gpu_ids(): 0
(pid=19844) CUDA_VISIBLE_DEVICES: 0


# Functions to Load Processed Data

In [4]:
def load_confirmed(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2 =df2.apply (pd.to_numeric, errors='coerce')
    df2 = df2.dropna()
    df2.index = pd.DatetimeIndex(df2.index)
    #interpolate missing data
    df2 = df2.reindex(pd.date_range(df2.index.min(), df2.index.max()), fill_value=np.nan)
    df2 = df2.interpolate(method='akima', axis=0).ffill().bfill()
    #string type for dates and integer for data
    df2 = df2.astype(int)
    df2.index = df2.index.astype(str)
    #select dates
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2 =df2.apply (pd.to_numeric, errors='coerce')
    df2 = df2.dropna()
    df2.index = pd.DatetimeIndex(df2.index)
    #interpolate missing data
    df2 = df2.reindex(pd.date_range(df2.index.min(), df2.index.max()), fill_value=np.nan)
    df2 = df2.interpolate(method='akima', axis=0).ffill().bfill()
    #string type for dates and integer for data
    df2 = df2.astype(int)
    df2.index = df2.index.astype(str)
    #select dates
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

# Load solver

In [5]:
import LearnerICRayNoLoadBH as L 

# Data for States

In [6]:
dfparam = pd.read_csv("data/param.csv")
dfPopEst = pd.read_csv("data/DRS_popEst.csv")
dfparam['popEst']=dfPopEst.popEst
display(dfparam)

DRS  start-date  prediction-range         s0  \
0        DRS 01 - Grande São Paulo  2020-03-20               200  2000000.0   
1               DRS 02 - Araçatuba  2020-04-01               200      500.0   
2              DRS 03 - Araraquara  2020-04-01               200     2000.0   
3        DRS 04 - Baixada Santista  2020-04-01               200     8000.0   
4                DRS 05 - Barretos  2020-04-01               200     2000.0   
5                   DRS 06 - Bauru  2020-04-01               200    10000.0   
6                DRS 07 - Campinas  2020-04-01               200    20000.0   
7                  DRS 08 - Franca  2020-04-01               200     1000.0   
8                 DRS 09 - Marília  2020-04-01               200     5000.0   
9              DRS 10 - Piracicaba  2020-04-01               200    10000.0   
10    DRS 11 - Presidente Prudente  2020-04-01               200     1000.0   
11               DRS 12 - Registro  2020-04-01               200     1000.0   
12         DRS 13 - Ribeirão Preto  2020-04-01               200     5000.0   
13  DRS 14 - São João da Boa Vista  2020-04-01               200     2000.0   
14  DRS 15 - São José do Rio Preto  2020-04-01               200    10000.0   
15               DRS 16 - Sorocaba  2020-04-01               200     1200.0   
16                DRS 17 - Taubaté  2020-04-01               200    10000.0   

        e0      a0        i0        r0        d0  START  RATIO  WCASES  WREC  \
0   0.0001  0.0001  800.0000  300.0000  400.0000      0   0.15    0.15  0.05   
1   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
2   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
3   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
4   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
5   0.0001  0.0001    4.0000    0.0001    0.0001      0   0.15    0.40  0.10   
6   0.0001  0.0001   40.0000    0.0001    0.0001      0   0.15    0.40  0.10   
7   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
8   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
9   0.0001  0.0001    0.0001    0.0001    1.0000      0   0.15    0.40  0.10   
10  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
11  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
12  0.0001  0.0001    0.0001    0.0001    0.0001      5   0.15    0.40  0.10   
13  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
14  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
15  0.0001  0.0001    2.0000    0.0001    0.0001      0   0.15    0.40  0.10   
16  0.0001  0.0001   17.0000    0.0001    2.0000      0   0.15    0.40  0.10   

        popEst  
0   21702084.0  
1     791256.0  
2    1025982.0  
3    1865397.0  
4     440907.0  
5    1800757.0  
6    4671287.0  
7     718176.0  
8    1146456.0  
9    1586546.0  
10    775627.0  
11    284509.0  
12   1523682.0  
13    834872.0  
14   1629470.0  
15   2530829.0  
16   2552610.0

In [7]:
dfSP = pd.read_csv("data/dados_municipios_SP.csv")

# lista DRSs
DRS = list(dfSP["DRS"].unique())
DRS.remove("Indefinido")

dfSP

date state   city place_type  confirmed  deaths  order_for_place  \
0      2020-09-12    SP  TOTAL      state     890690   32567              199   
1      2020-09-11    SP  TOTAL      state     882809   32338              198   
2      2020-09-10    SP  TOTAL      state     874754   32104              197   
3      2020-09-09    SP  TOTAL      state     866576   31821              196   
4      2020-09-08    SP  TOTAL      state     858783   31430              195   
...           ...   ...    ...        ...        ...     ...              ...   
82538  2020-06-23    SP   Óleo       city          1       0                5   
82539  2020-06-22    SP   Óleo       city          1       0                4   
82540  2020-06-21    SP   Óleo       city          1       0                3   
82541  2020-06-20    SP   Óleo       city          1       0                2   
82542  2020-06-19    SP   Óleo       city          1       0                1   

       is_last      popEst  city_ibge_code  confirmed_per_100k_inhabitants  \
0         True  45919049.0            35.0                      1939.69609   
1        False  45919049.0            35.0                      1922.53328   
2        False  45919049.0            35.0                      1904.99154   
3        False  45919049.0            35.0                      1887.18194   
4        False  45919049.0            35.0                      1870.21077   
...        ...         ...             ...                             ...   
82538    False      2496.0       3533809.0                        40.06410   
82539    False      2496.0       3533809.0                        40.06410   
82540    False      2496.0       3533809.0                        40.06410   
82541    False      2496.0       3533809.0                        40.06410   
82542    False      2496.0       3533809.0                        40.06410   

       death_rate               DRS  
0          0.0366        Indefinido  
1          0.0366        Indefinido  
2          0.0367        Indefinido  
3          0.0367        Indefinido  
4          0.0366        Indefinido  
...           ...               ...  
82538      0.0000  DRS 09 - Marília  
82539      0.0000  DRS 09 - Marília  
82540      0.0000  DRS 09 - Marília  
82541      0.0000  DRS 09 - Marília  
82542      0.0000  DRS 09 - Marília  

[82543 rows x 13 columns]

# Functions for Optimization

In [8]:
from scipy.integrate import odeint
import sys
import io
import gc

def create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version):
                
    def fobjective(point):
        
        dead=  load_dead(districtRegion,date)
        data = load_confirmed(districtRegion,date)*(1-ratio)-dead
        cleanRecovered=False
        s0, deltaDate, i0, d0, startNCases, weigthCases, weigthRecov = point
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=deltaDate)
        f=L.Learner.remote(districtRegion, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, data, dead, point,f         

        gc.collect()

        return result
    return fobjective

In [9]:
@ray.remote(memory=50 * 1024 * 1024, max_calls=1)
def opt(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, 
        ratio, predict_range, popEst, version):

    bounds=[(0.05*popEst,0.4*popEst),(-2,2),(0,250), (0,100), (0,150),\
              (0.05,0.7),(0.001,0.05)]
    maxiterations=500
    f=create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version)
    de = DE(f, bounds, maxiters=maxiterations)
    for step in de.geniterator():
        try:
            idx = step.best_idx
            norm_vector = step.population[idx]
            best_params = de.denormalize([norm_vector])
            del norm_vector, idx
        except:
            print("error in function evaluation")
    p=best_params[0]
    del f, bounds, data, dead,best_params
    
    return p

# Main Code

In [10]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines){
    return true;}

<IPython.core.display.Javascript object>

In [11]:
DRS=dfparam.DRS
display(DRS)
allDRS=True
version="110"
gc.enable()

optimal=[]
if allDRS:
    for districtRegion in DRS:
        #remove previous history file
        strFile='./results/history_'+districtRegion+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
        optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, \
                                  ratio, predict_range, popEst, version))        
else:
    districtRegion = "DRS 01 - Grande São Paulo" #'DRS 08 - Franca' \
    #'DRS 14 - São João da Boa Vista' #'DRS 04 - Baixada Santista' \
    #'DRS 11 - Presidente Prudente' #'DRS 13 - Ribeirão Preto' \
    #'DRS 05 - Barretos' #'DRS 12 - Registro' #'DRS 15 - São José do Rio Preto' \
    #'DRS 10 - Piracicaba'#'DRS 17 - Taubaté'#'DRS 02 - Araçatuba'# \
    #'DRS 03 - Araraquara' #DRS 07 - Campinas'#'DRS 16 - Sorocaba'#'DRS 06 - Bauru' \
    #'DRS 09 - Marília' #"DRS 01 - Grande São Paulo"

    #remove previous history file
    strFile='./results/history_'+districtRegion+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
    optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcasesdate,startNCases, \
                              ratio, predict_range, popEst, version))        

0          DRS 01 - Grande São Paulo
1                 DRS 02 - Araçatuba
2                DRS 03 - Araraquara
3          DRS 04 - Baixada Santista
4                  DRS 05 - Barretos
5                     DRS 06 - Bauru
6                  DRS 07 - Campinas
7                    DRS 08 - Franca
8                   DRS 09 - Marília
9                DRS 10 - Piracicaba
10      DRS 11 - Presidente Prudente
11                 DRS 12 - Registro
12           DRS 13 - Ribeirão Preto
13    DRS 14 - São João da Boa Vista
14    DRS 15 - São José do Rio Preto
15                 DRS 16 - Sorocaba
16                  DRS 17 - Taubaté
Name: DRS, dtype: object

In [ ]:
optimal=ray.get(optimal)


2020-09-13 11:15:54,820	WARNING worker.py:1090 -- WARNING: 3 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-09-13 11:15:55,685	WARNING worker.py:1090 -- WARNING: 4 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-09-13 11:15:56,073	WARNING worker.py:1090 -- WARNING: 5 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-09-13 11:15:56,934	WARNING worker.py:1090 -- WARNING: 6 PYTHON workers have been started. This could be a resu

(pid=19914) basinhopping step 0: f 1.61484e+07


2020-09-13 11:15:58,218	WARNING worker.py:1090 -- WARNING: 8 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-09-13 11:15:58,634	WARNING worker.py:1090 -- WARNING: 9 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-09-13 11:15:59,506	WARNING worker.py:1090 -- WARNING: 10 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-09-13 11:15:59,902	WARNING worker.py:1090 -- WARNING: 11 PYTHON workers have been started. This could be a re

(pid=19966) basinhopping step 0: f 9.36239e+07


2020-09-13 11:16:02,031	WARNING worker.py:1090 -- WARNING: 14 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


...

2020-09-13 14:18:36,828	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=11241) basinhopping step 4: f 1.41872e+07 trial_f 1.41872e+07 accepted 1  lowest_f 1.41872e+07
(pid=11241) found new global minimum on step 4 with function value 1.41872e+07
(pid=11228) basinhopping step 5: f -7.39843e+09 trial_f 8.17947e+06 accepted 0  lowest_f -7.39843e+09
(pid=11267) basinhopping step 6: f -1.98961e+11 trial_f 8.86173e+07 accepted 0  lowest_f -1.98961e+11
(pid=11174) basinhopping step 4: f -7.29455e+12 trial_f 4.58177e+10 accepted 0  lowest_f -7.29455e+12
(pid=11215) basinhopping step 6: f -1.86729e+11 trial_f 4.23888e+08 accepted 0  lowest_f -1.86729e+11
(pid=11041) basinhopping step 8: f -2.18568e+10 trial_f 8.12182e+06 accepted 0  lowest_f -2.18568e+10
(pid=11254) basinhopping step 2: f -3.93352e+11 trial_f -3.93352e+11 accepted 1  lowest_f -3.93352e+11
(pid=11254) found new global minimum on step 2 with function value -3.93352e+11
(pid=11106) basinhopping step 7: f -1.2032e+10 trial_f -6.72129e+09 accepted 0  lowest_f -1.2032e+10
(pid=11254) warning: basinh

2020-09-13 14:18:44,495	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=11294) basinhopping step 3: f 711113 trial_f 6.47933e+07 accepted 0  lowest_f 711113
(pid=11280) basinhopping step 4: f -1.27982e+10 trial_f 8.14628e+06 accepted 0  lowest_f -1.27982e+10
(pid=11228) basinhopping step 6: f -7.39843e+09 trial_f -1.80109e+07 accepted 0  lowest_f -7.39843e+09
(pid=11294) basinhopping step 4: f 711113 trial_f 1.73892e+07 accepted 0  lowest_f 711113
(pid=11215) basinhopping step 7: f -1.86729e+11 trial_f 9.27733e+07 accepted 0  lowest_f -1.86729e+11
(pid=11280) basinhopping step 5: f -1.27982e+10 trial_f 6.55303e+06 accepted 0  lowest_f -1.27982e+10
(pid=11320) basinhopping step 0: f -1.1639e+11
(pid=11320) basinhopping step 1: f -1.1639e+11 trial_f 1.01402e+11 accepted 0  lowest_f -1.1639e+11
(pid=11267) basinhopping step 7: f -1.98961e+11 trial_f 8.56535e+08 accepted 0  lowest_f -1.98961e+11
(pid=11346) basinhopping step 0: f -7.55582e+09
(pid=11320) basinhopping step 2: f -1.1639e+11 trial_f 1.01403e+11 accepted 0  lowest_f -1.1639e+11
(pid=11320) ba

2020-09-13 14:18:55,514	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


In [ ]:
for i in range(0,len(DRS)):    

    districtRegion=DRS[i]
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")

    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]

    dfparam.to_csv("data/param_optimized_Yabox.csv", sep=",", index=False)
    dfparam
    